In [1]:
import numpy as np

import sys
sys.path.append("../")
from koopmanlib.dictionary import PsiNN

In [2]:
basis_function = PsiNN(layer_sizes=[100,100,100], n_psi_train=100)

In [3]:
from duffing_oscillator import duffing_oscillator
from scipy.integrate import solve_ivp

# Parameters
delta = 0.5
alpha = -1
beta = 1

# Sample N=1000 initial points, with uniform distribution [-2, 2].
N = 1000
np.random.seed(39)
sample_data_x0 = (np.random.rand(N, 2) * 4) - 2

tspan = [0, 2.5]
nstep = 11
data = np.zeros((N, 2, nstep))

t_eval = np.linspace(tspan[0], tspan[1], nstep)

for idx, x0 in enumerate(sample_data_x0):
    sol = solve_ivp(duffing_oscillator, tspan, x0, t_eval=t_eval, args=(delta, alpha, beta))
    data[idx, 0, :] = sol.y[0]
    data[idx, 1, :] = sol.y[1]

# Pairwise shifted data X and Y
X = data[:, :, :-1] # shape: (1000, 2, 10)
Y = data[:, :, 1:]
print(X.shape, type(X))
print(Y.shape, type(Y))

# Transpose and reshape the data.
X = np.transpose(X, (0, 2, 1)).reshape(N * (nstep-1), 2) # shape: (10000, 2)
Y = np.transpose(Y, (0, 2, 1)).reshape(N * (nstep-1), 2)
print(X.shape, type(X))
print(Y.shape, type(Y))

(1000, 2, 10) <class 'numpy.ndarray'>
(1000, 2, 10) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>


In [4]:
len_all = X.shape[0]
data_x_train = X[:int(0.7*len_all),:]
data_x_valid = X[int(0.7*len_all)+1:,:]

data_y_train = Y[:int(0.7*len_all),:]
data_y_valid = Y[int(0.7*len_all)+1:,:]

In [5]:
data_train = [data_x_train, data_y_train]
data_valid = [data_x_valid, data_y_valid]

In [14]:
from koopmanlib.solver_0 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 152ms/step - loss: 0.0067 - val_loss: 0.0023
Epoch 2/2
2/2 [==============================] - 0s 35ms/step - loss: 0.0065 - val_loss: 0.0131
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 60ms/step - loss: 2.5970e-04 - val_loss: 8.5256e-04
Epoch 2/2
2/2 [==============================] - 0s 33ms/step - loss: 7.4523e-04 - val_loss: 3.1438e-04
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 58ms/step - loss: 1.3067e-04 - val_loss: 4.8124e-04
Epoch 2/2
2/2 [==============================] - 0s 35ms/step - loss: 4.1654e-04 - val_loss: 1.2707e-04
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 60ms/step - loss: 1.0292e-04 - val_loss: 2.9254e-04
Epoch 2/2
2/2 [==============================] - 0s 36ms/step - loss: 2.5804e-04 - val_loss: 8.8878e-05
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 59ms/step - loss: 8

In [15]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs0 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs0['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs0['resDMD_DL_outputs']['efuns'].shape)

[ 1.00073419e+00+0.00000000e+00j  9.99965914e-01+0.00000000e+00j
  8.25964889e-01+0.00000000e+00j  8.16012863e-01+1.61575108e-01j
  8.16012863e-01-1.61575108e-01j  7.95098326e-01+3.45345284e-01j
  7.95098326e-01-3.45345284e-01j  7.63331475e-01+3.67744646e-01j
  7.63331475e-01-3.67744646e-01j  5.53056043e-01+4.46591507e-01j
  5.53056043e-01-4.46591507e-01j  5.40214751e-01+0.00000000e+00j
  3.38487445e-01-3.89610363e-01j  3.38487445e-01+3.89610363e-01j
  3.01165238e-01+1.49163824e-01j  3.01165238e-01-1.49163824e-01j
  1.10612890e-01-6.45668766e-01j  1.10612890e-01+6.45668766e-01j
  9.19938347e-02+7.31129916e-02j  9.19938347e-02-7.31129916e-02j
  7.91512346e-02+0.00000000e+00j  3.56960936e-02+0.00000000e+00j
  1.53903874e-02+0.00000000e+00j  4.94862075e-03+4.66622537e-03j
  4.94862075e-03-4.66622537e-03j  2.04189111e-03+0.00000000e+00j
  1.92777011e-03+4.59083216e-03j  1.92777011e-03-4.59083216e-03j
  1.17586661e-03+0.00000000e+00j  3.58329653e-04+0.00000000e+00j
  9.56258283e-05+0.000000

In [12]:
from koopmanlib.solver_1 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 31s 5s/step - loss: 0.8980 - val_loss: 0.9003
Epoch 2/2
2/2 [==============================] - 1s 309ms/step - loss: 0.9001 - val_loss: 0.9048
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 325ms/step - loss: 0.8976 - val_loss: 0.8969
Epoch 2/2
2/2 [==============================] - 0s 296ms/step - loss: 0.8936 - val_loss: 0.8931
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 1s 325ms/step - loss: 0.8911 - val_loss: 0.8919
Epoch 2/2
2/2 [==============================] - 1s 322ms/step - loss: 0.8945 - val_loss: 0.8966
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 1s 335ms/step - loss: 0.8930 - val_loss: 0.8806
Epoch 2/2
2/2 [==============================] - 0s 296ms/step - loss: 0.8890 - val_loss: 0.8938
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 1s 348ms/step - loss: 0.8938 - val_loss: 0.8900
Epoch 2/2
2/2 [==

In [13]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs1 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs1['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs1['resDMD_DL_outputs']['efuns'].shape)

[ 1.01921178e+00+0.00000000e+00j  9.99968237e-01+0.00000000e+00j
  8.53820162e-01+0.00000000e+00j  8.19891481e-01-1.67032559e-01j
  8.19891481e-01+1.67032559e-01j  8.05338017e-01+0.00000000e+00j
  7.84313747e-01+3.87116589e-01j  7.84313747e-01-3.87116589e-01j
  7.31528398e-01+4.77499207e-01j  7.31528398e-01-4.77499207e-01j
  6.18027052e-01+2.33882077e-01j  6.18027052e-01-2.33882077e-01j
  5.02404385e-01+0.00000000e+00j  4.15454259e-01-1.12207715e-01j
  4.15454259e-01+1.12207715e-01j  3.69100216e-01-5.38600186e-01j
  3.69100216e-01+5.38600186e-01j  1.80567005e-01-3.50831807e-01j
  1.80567005e-01+3.50831807e-01j  1.01745443e-01+0.00000000e+00j
  3.20310228e-02+5.95465906e-03j  3.20310228e-02-5.95465906e-03j
  1.26382813e-02+0.00000000e+00j  9.89874349e-03+3.48006761e-02j
  9.89874349e-03-3.48006761e-02j  8.80463390e-03-1.49614989e-03j
  8.80463390e-03+1.49614989e-03j  6.75648951e-04+0.00000000e+00j
  1.10912209e-04+2.77585002e-04j  1.10912209e-04-2.77585002e-04j
  9.40639803e-05+0.000000

In [10]:
from koopmanlib.solver_2 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 253ms/step - loss: 2272926.8750 - val_loss: 1556530.2500
Epoch 2/2
2/2 [==============================] - 0s 101ms/step - loss: 1990931.0536 - val_loss: 1373194.1250
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 118ms/step - loss: 1743760.0714 - val_loss: 1213825.0000
Epoch 2/2
2/2 [==============================] - 0s 102ms/step - loss: 1550946.5357 - val_loss: 1076097.0000
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 123ms/step - loss: 1370644.9464 - val_loss: 957838.8125
Epoch 2/2
2/2 [==============================] - 0s 107ms/step - loss: 1219224.9732 - val_loss: 856458.1250
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 124ms/step - loss: 1099616.4196 - val_loss: 770013.6875
Epoch 2/2
2/2 [==============================] - 0s 101ms/step - loss: 986126.4911 - val_loss: 696449.0625
number of the outer loop: 3
Epoch 1/2
2/2 [======

In [11]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs2 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs2['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs2['resDMD_DL_outputs']['efuns'].shape)

[ 1.00002071e+00+0.00000000e+00j  9.93742628e-01+0.00000000e+00j
  8.27356288e-01+0.00000000e+00j  8.05231419e-01+2.05716064e-01j
  8.05231419e-01-2.05716064e-01j  7.66482538e-01+3.91329109e-01j
  7.66482538e-01-3.91329109e-01j  7.26219721e-01+0.00000000e+00j
  5.85347925e-01+5.25429383e-01j  5.85347925e-01-5.25429383e-01j
  4.18982418e-01+0.00000000e+00j  1.80092741e-01+9.99193747e-02j
  1.80092741e-01-9.99193747e-02j  1.34557141e-01+1.33884584e-01j
  1.34557141e-01-1.33884584e-01j  1.19763112e-01-1.81902678e-01j
  1.19763112e-01+1.81902678e-01j  3.82660938e-02+0.00000000e+00j
  2.41123055e-02-3.84975006e-01j  2.41123055e-02+3.84975006e-01j
  1.74002960e-02+0.00000000e+00j  1.26788021e-02+0.00000000e+00j
  6.99697367e-04+4.58806589e-04j  6.99697367e-04-4.58806589e-04j
  6.38300248e-04+0.00000000e+00j  3.00725463e-04+3.76083350e-04j
  3.00725463e-04-3.76083350e-04j  2.05331663e-04+1.57305690e-04j
  2.05331663e-04-1.57305690e-04j  1.05708987e-04+0.00000000e+00j
  4.01891028e-05+3.704074

In [6]:
from koopmanlib.solver_3 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 286ms/step - loss: 2.6209e-05 - val_loss: 0.0013
Epoch 2/2
2/2 [==============================] - 0s 107ms/step - loss: 8.5066e-04 - val_loss: 3.0844e-04
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 123ms/step - loss: 1.1153e-04 - val_loss: 3.3952e-04
Epoch 2/2
2/2 [==============================] - 0s 96ms/step - loss: 2.7212e-04 - val_loss: 3.2252e-05
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 125ms/step - loss: 3.7796e-05 - val_loss: 1.8329e-04
Epoch 2/2
2/2 [==============================] - 0s 94ms/step - loss: 1.6041e-04 - val_loss: 5.7457e-05
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 123ms/step - loss: 1.8675e-05 - val_loss: 7.8650e-05
Epoch 2/2
2/2 [==============================] - 0s 98ms/step - loss: 6.9116e-05 - val_loss: 3.2642e-05
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 121

In [7]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs3 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs3['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs3['resDMD_DL_outputs']['efuns'].shape)

[ 1.01883006e+00+0.00000000e+00j  9.99998711e-01+0.00000000e+00j
  8.49958700e-01+1.59300071e-01j  8.49958700e-01-1.59300071e-01j
  7.53970995e-01+4.24383234e-01j  7.53970995e-01-4.24383234e-01j
  6.92034377e-01+2.86040384e-01j  6.92034377e-01-2.86040384e-01j
  4.95249614e-01+0.00000000e+00j  3.98621831e-01+5.29734291e-01j
  3.98621831e-01-5.29734291e-01j  9.36429551e-02-3.47855281e-02j
  9.36429551e-02+3.47855281e-02j  5.13797480e-02-6.25201346e-02j
  5.13797480e-02+6.25201346e-02j  4.05168938e-02+0.00000000e+00j
  3.25985217e-02-1.58077367e-02j  3.25985217e-02+1.58077367e-02j
  2.13604945e-02+0.00000000e+00j  1.11228552e-02+6.53473164e-01j
  1.11228552e-02-6.53473164e-01j  3.11590172e-03+0.00000000e+00j
  4.25551431e-04+0.00000000e+00j  2.19677909e-04+4.13403999e-06j
  2.19677909e-04-4.13403999e-06j  1.50515560e-04+2.59301009e-04j
  1.50515560e-04-2.59301009e-04j  1.33700327e-04+0.00000000e+00j
  6.24571956e-05+0.00000000e+00j  1.84036223e-05+0.00000000e+00j
  1.69391688e-05+4.399241

In [8]:
from koopmanlib.solver_4 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 255ms/step - loss: 0.4057 - val_loss: 0.2050
Epoch 2/2
2/2 [==============================] - 0s 89ms/step - loss: 0.2486 - val_loss: 0.2737
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 119ms/step - loss: 0.9326 - val_loss: 0.2357
Epoch 2/2
2/2 [==============================] - 0s 90ms/step - loss: 0.9192 - val_loss: 0.2856
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 110ms/step - loss: 0.8735 - val_loss: 0.3443
Epoch 2/2
2/2 [==============================] - 0s 100ms/step - loss: 0.6358 - val_loss: 0.2851
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 118ms/step - loss: 0.1153 - val_loss: 0.1470
Epoch 2/2
2/2 [==============================] - 0s 94ms/step - loss: 0.8566 - val_loss: 0.2902
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 109ms/step - loss: 1.7402 - val_loss: 0.0527
Epoch 2/2
2/2 [===

In [9]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs4 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs4['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs4['resDMD_DL_outputs']['efuns'].shape)

[ 1.01882529e+00+0.00000000e+00j  9.99998708e-01+0.00000000e+00j
  8.49869295e-01+1.59263134e-01j  8.49869295e-01-1.59263134e-01j
  7.54017963e-01+4.24339328e-01j  7.54017963e-01-4.24339328e-01j
  6.91702654e-01+2.86005834e-01j  6.91702654e-01-2.86005834e-01j
  4.96574744e-01+0.00000000e+00j  3.98654356e-01+5.29646434e-01j
  3.98654356e-01-5.29646434e-01j  9.41879251e-02+3.45213343e-02j
  9.41879251e-02-3.45213343e-02j  5.16313242e-02+6.26520074e-02j
  5.16313242e-02-6.26520074e-02j  3.61760202e-02+0.00000000e+00j
  3.29808033e-02-1.63572502e-02j  3.29808033e-02+1.63572502e-02j
  2.07838495e-02+0.00000000e+00j  1.09646622e-02+6.53440200e-01j
  1.09646622e-02-6.53440200e-01j  3.12545427e-03+0.00000000e+00j
  4.31496474e-04+0.00000000e+00j  2.07742586e-04+1.62680858e-05j
  2.07742586e-04-1.62680858e-05j  1.47060299e-04+2.52764391e-04j
  1.47060299e-04-2.52764391e-04j  1.35244536e-04+0.00000000e+00j
  6.34738402e-05+0.00000000e+00j  1.84771712e-05+0.00000000e+00j
  1.60052711e-05+4.301812